In [15]:
from sklearn.tree import DecisionTreeClassifier, export_graphviz
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import ExtraTreesClassifier
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import accuracy_score
from sklearn.naive_bayes import GaussianNB
from IPython.display import Image
import pandas as pd 
import numpy as np	
import itertools
import pydotplus

In [2]:
dataset = pd.read_csv('/Users/farrelmanazilin/Document/kuliah/data/water_potability.csv')
print('Datasett\n',dataset)
dataset = dataset.fillna(dataset.groupby("Potability").transform('mean'))

Datasett
             ph    Hardness       Solids  Chloramines     Sulfate   
0          NaN  204.890456  20791.31898     7.300212  368.516441  \
1     3.716080  129.422921  18630.05786     6.635246         NaN   
2     8.099124  224.236259  19909.54173     9.275884         NaN   
3     8.316766  214.373394  22018.41744     8.059332  356.886136   
4     9.092223  181.101509  17978.98634     6.546600  310.135738   
...        ...         ...          ...          ...         ...   
3271  4.668102  193.681736  47580.99160     7.166639  359.948574   
3272  7.808856  193.553212  17329.80216     8.061362         NaN   
3273  9.419510  175.762646  33155.57822     7.350233         NaN   
3274  5.126763  230.603758  11983.86938     6.303357         NaN   
3275  7.874671  195.102299  17404.17706     7.509306         NaN   

      Conductivity  Organic_carbon  Trihalomethanes  Turbidity  Potability  
0       564.308654       10.379783        86.990970   2.963135           0  
1       592.885359 

In [3]:
all_features = dataset.columns[:-1]
best_average_accuracy = 0
best_feature_names = None
best_method = None

accuracies = []

for r in range(1, len(all_features) + 1):
    for feature_indices in itertools.combinations(all_features, r):
        X = dataset[list(feature_indices)]
        Y = dataset['Potability']

        X_train, X_test, y_train, y_test = train_test_split(X, Y, test_size=0.3, random_state=100)

        scaler = MinMaxScaler()
        X_train_normalized = scaler.fit_transform(X_train)
        X_test_normalized = scaler.transform(X_test)

        knn = KNeighborsClassifier()
        knn.fit(X_train_normalized, y_train)
        knn_pred = knn.predict(X_test_normalized)
        knn_accuracy = accuracy_score(y_test, knn_pred)

        nb = GaussianNB()
        nb.fit(X_train_normalized, y_train)
        nb_pred = nb.predict(X_test_normalized)
        nb_accuracy = accuracy_score(y_test, nb_pred)

        dt = DecisionTreeClassifier()
        dt.fit(X_train_normalized, y_train)
        dt_pred = dt.predict(X_test_normalized)
        dt_accuracy = accuracy_score(y_test, dt_pred)

        average_accuracy = (knn_accuracy + nb_accuracy + dt_accuracy) / 3

        accuracies.append(("KNN", feature_indices, knn_accuracy))
        accuracies.append(("Naive Bayes", feature_indices, nb_accuracy))
        accuracies.append(("Decision Tree", feature_indices, dt_accuracy))

        if average_accuracy > best_average_accuracy:
            best_average_accuracy = average_accuracy
            best_feature_names = feature_indices
            best_method = "Average of KNN, Naive Bayes, and Decision Tree"
print(f"Kombinasi Fitur Terbaik: {list(best_feature_names)}")
print(f"Rata-rata Akurasi Terbaik: {best_average_accuracy}")


Kombinasi Fitur Terbaik: ['ph', 'Hardness', 'Chloramines', 'Sulfate']
Rata-rata Akurasi Terbaik: 0.6893862326212276


In [16]:
X = dataset.loc[:, list(best_feature_names)]
Y = dataset['Potability']

X_train, X_test, y_train, y_test = train_test_split(X, Y, test_size=0.3, random_state=100)

scaler = MinMaxScaler()
X_train_normalized = scaler.fit_transform(X_train)
X_test_normalized = scaler.transform(X_test)

In [17]:
kNN = KNeighborsClassifier(n_neighbors=3, weights='distance')
kNN.fit(X_train_normalized, y_train.values.ravel())  
y_pred = kNN.predict(X_test_normalized)

accuracy = accuracy_score(y_test, y_pred)
error_ratio_holdout = 1 - accuracy

print("Akurasi ratio untuk metode KNN (30-70%): {:.10f}".format(accuracy ))
print("Error ratio untuk metode KNN (30-70%): {:.10f}".format(error_ratio_holdout))

Akurasi ratio untuk metode KNN (30-70%): 0.6480162767
Error ratio untuk metode KNN (30-70%): 0.3519837233


In [18]:
classifier = GaussianNB()
classifier.fit(X_train_normalized, y_train)
ypred = classifier.predict(X_test_normalized)

accuracy = accuracy_score(y_test, ypred)
error_ratio_holdout = 1 - accuracy

print("Akurasi untuk metode Naive Bayes (70-30%): {:.10f}".format(accuracy))
print("Error ratio untuk metode Naive Bayes (70-30%): {:.10f}".format(error_ratio_holdout))

Akurasi untuk metode Naive Bayes (70-30%): 0.6286876907
Error ratio untuk metode Naive Bayes (70-30%): 0.3713123093


In [21]:
dtc = DecisionTreeClassifier()
dtc.fit(X_train_normalized, y_train)

class_result = dtc.predict(X_test_normalized)
print('Class = ', class_result)

acc = dtc.score(X_test_normalized, y_test)
err = 1 - acc
print("\n\nAkurasi untuk metode Decision Tree (70-30%): {:.10f}".format(acc))
print("Error ratio untuk metode Decision Tree (70-30%): {:.10f}".format(err))


Class =  [1 1 0 1 0 0 0 1 1 0 1 1 1 0 1 1 1 1 0 0 0 1 0 0 0 1 0 1 0 0 1 0 1 0 0 0 1
 1 0 0 1 1 0 1 0 1 0 1 1 0 0 0 0 0 1 0 0 1 1 1 0 1 1 1 0 0 0 1 0 1 0 0 1 0
 0 0 0 1 1 0 1 0 1 0 1 0 0 0 1 0 1 0 0 0 1 0 1 1 0 1 0 0 0 0 0 1 1 0 1 0 1
 0 0 0 1 0 0 0 1 1 0 0 1 0 1 1 0 0 0 1 1 1 1 1 0 0 0 1 0 0 0 1 0 1 1 0 1 0
 0 1 0 1 0 1 0 1 0 0 0 0 1 0 0 1 0 0 1 0 0 0 0 0 1 0 1 1 0 1 1 0 0 0 1 1 0
 0 1 0 1 0 0 0 1 0 1 1 0 0 0 1 0 1 1 1 1 0 1 0 1 0 1 1 0 1 1 0 0 0 0 1 0 0
 0 0 0 0 0 0 1 0 0 0 0 0 1 0 1 1 0 0 1 0 1 0 0 1 0 0 0 0 0 0 1 0 0 1 0 0 0
 0 1 0 1 1 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 1 1 0 1 1 0 1 0 1 0 1 0 0
 0 0 0 0 0 0 1 0 0 0 0 1 1 1 1 0 1 0 1 0 0 0 0 0 1 1 1 1 0 1 1 0 1 0 1 0 0
 0 0 0 0 1 0 0 0 0 1 1 0 0 0 0 0 1 0 1 0 0 1 1 0 0 1 0 1 0 0 1 0 0 1 0 0 1
 0 0 0 1 1 0 0 0 1 0 1 0 0 0 1 0 0 0 1 1 1 1 1 1 0 0 0 0 0 0 0 0 1 1 0 1 1
 1 0 0 0 1 0 0 1 1 0 1 0 0 0 0 0 0 1 0 0 0 1 1 0 1 0 0 0 1 0 1 1 1 0 0 0 0
 0 0 1 1 0 0 0 0 0 0 0 0 0 1 0 0 0 1 1 0 0 0 0 0 0 1 1 1 0 1 0 1 0 0 0 1 0
 0 0 0 0 0 0 0 0

In [ ]:
dot_data = export_graphviz(
    dtc,  
    out_file=None,
    feature_names= list(best_feature_names),
    class_names=[str(label) for label in y_train.unique()],
    filled=True,
    rounded=True,
    special_characters=True
)
graph = pydotplus.graph_from_dot_data(dot_data)
graph.write_png("decision_tree.png")
Image(graph.create_png())